In [ ]:
import numpy as np
import pandas as pd
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

# **Data**

We´ll work with three simple datasets to demonstrate how our models work:


1.   A normal random distribution of data in two dimensions
2.   A normal, *donut*-like distribution
3.   An XOR logic function distribution





In [ ]:
# Dataset 1
N = 4000  # Observations
k = 5     # Number of blobs
dims = 2  # Number of dimensions of data

df1 = []  # Our dataset

# We´ll create 5 blobs of data with a normal distribution
for i in range(k):
  df1.append(np.random.randn(N,dims) + np.random.randn(1,dims)*5.2)

df1 = np.vstack(df1)  # Arrange vertically
df1

array([[14.79080307, -1.54051388],
       [15.40262933, -2.5060144 ],
       [16.31328741, -2.91032027],
       ...,
       [-6.06163267, -1.67403936],
       [-4.77825906, -1.8628091 ],
       [-5.2802061 , -2.40443861]])

In [ ]:
fig = px.scatter(x = df1[:,0],
               y = df1[:,1],
               title = 'Random dataset (dataset 1)')
fig.show()

In [ ]:
# Dataset 2
df2 = pd.read_csv('data/donut.csv',
                  sep = ' ',
                  header = None)
df2

0         1    2
0     1.823942 -0.114612  0.0
1     0.750285  1.064485  0.0
2     1.577961  1.125408  0.0
3     0.393252 -0.547694  0.0
4     2.463079 -0.848993  0.0
...        ...       ...  ...
3995  5.870650 -1.606308  1.0
3996  4.733952  0.127538  1.0
3997  6.593012 -1.708109  1.0
3998  4.404825 -0.115727  1.0
3999  4.045071  0.095259  1.0

[4000 rows x 3 columns]

In [ ]:
fig = px.scatter(x = df2[0],
               y = df2[1],
               color = df2[2],
               title = 'Donut dataset (dataset 2)')
fig.update_coloraxes(showscale=False)
fig.show()

In [ ]:
# Dataset 3
df3 = pd.read_csv('data/xor.csv')
df3

x1        x2  y
0     1.907567  0.325865  0
1     2.270544  2.258817  0
2     2.323086  1.466601  0
3     0.752419  2.684305  0
4     2.837229  2.238149  0
...        ...       ... ..
3995  2.274223 -2.579655  1
3996  1.541694 -1.140535  1
3997  3.059691 -2.873532  1
3998  3.525607 -2.331070  1
3999  1.720059 -1.134640  1

[4000 rows x 3 columns]

In [ ]:
fig = px.scatter(x = df3['x1'],
               y = df3['x2'],
               color = df3['y'],
               title = 'XOR dataset (dataset 3)')
fig.update_coloraxes(showscale=False)
fig.show()

# **K-Means Clustering**
This unsupervised method looks to group data points into a particular class based on the mean distance it has with a given reference.

This model works assuming that the data follows a normal distribution. Also, it only groups the data based on a random center (at first), so this model is actually **not learning the best distribution**. That means that there´s no loss function that will determine if the model improves or not while using more iterations.

# Step 1: Select your centers
Before grouping, we need to define how many groups we´ll use, and where their centroids will be located. Since we don´t have any reference, we just select random points.

We´ll use the first dataset for the explanations.

In [ ]:
means = []  # Our centroids
k = 5       # Number of classes

indices = np.arange(df1.shape[0]) # We get the indices of all our datapoints
sample_indices = np.random.choice(indices, size = k, replace = False) # Select 5 random indices
means = df1[sample_indices] # Assign those points as centroids
means

array([[-4.89717272, -1.85891891],
       [-0.85986414,  5.95570019],
       [ 1.35976127,  9.85588869],
       [-5.0184292 , -1.4750079 ],
       [-6.92499184, -0.35685312]])

In [ ]:
fig = go.Figure()

# Our dataset
fig.add_trace(go.Scatter(x = df1[:,0],
                         y = df1[:,1],
                         mode = 'markers'))
# Our centroids
fig.add_trace(go.Scatter(x = means[:,0],
                         y = means[:,1],
                         mode = 'markers'))

fig.update_layout(showlegend=False)
fig.show()

# Step 2: Get the distance between points
The most common approach is using the Euclidean distance between two points. However, the K-Means algorithm can work with any other distance metric.

For each datapoint, you'll get its distance with all the current centroids, and you'll assign it to the closest.

In [ ]:
"""
X - all the datapoints
means - your current centroids
"""
def distance(X, means):
  diff = [] # Differences between points
  dists = []  # Euclidean distances of the points

  for mean in means:
    diff = X - mean
    dist = np.sqrt(np.sum(diff**2, axis=1, keepdims=True))
    dists.append(dist)

  return np.hstack(dists)

In [ ]:
dist = distance(df1, means)
dist

array([[19.69055034, 17.35328815, 17.61450753, 19.80934058, 21.74802983],
       [20.31011314, 18.33219321, 18.70878915, 20.4470684 , 22.43081723],
       [21.23650309, 19.32675484, 19.66174039, 21.37994984, 23.37814828],
       ...,
       [ 1.17904513,  9.2342472 , 13.71190464,  1.06202025,  1.57491862],
       [ 0.11897727,  8.7454506 , 13.22887643,  0.45614851,  2.62228241],
       [ 0.66656305,  9.45681467, 13.94291189,  0.96559234,  2.62639039]])

In [ ]:
# Each point will be assigned to the class with the less distance
y_hat = np.argmin(dist, axis=1)

fig = go.Figure()

# Show the centroids
fig.add_trace(go.Scatter(x = df1[:,0],
                         y = df1[:,1],
                         mode = 'markers',
                         marker = dict(color = y_hat),
                         showlegend = False))

# Print the datapoints based on their current class
fig.add_trace(go.Scatter(x = means[:,0],
                         y = means[:,1],
                         mode = 'markers',
                         marker = dict(color = 'black'),
                         showlegend = False))

# fig.update_coloraxes(showscale=False)
fig.show()

# Step 3: Update the centroids
Once you have an initial classification, you can update the centroids baseed on those groups, and reclassify your data based on them.

You need to repeat this process $N$ times (or until you think it´s done).

In [ ]:
# Forget the previous centroids
means = []

# Recalculate them based on your current classes
for i in range(k):
  mean = np.mean(df1[y_hat==i], axis=0)
  means.append(mean)

means = np.vstack(means)

In [ ]:
dist = distance(df1, means)
dist

# Each point will be assigned to the class with the less distance
y_hat = np.argmin(dist, axis=1)

fig = go.Figure()

# Show the centroids
fig.add_trace(go.Scatter(x = df1[:,0],
                         y = df1[:,1],
                         mode = 'markers',
                         marker = dict(color = y_hat),
                         showlegend = False))

# Print the datapoints based on their current class
fig.add_trace(go.Scatter(x = means[:,0],
                         y = means[:,1],
                         mode = 'markers',
                         marker = dict(color = 'black'),
                         showlegend = False))

# fig.update_coloraxes(showscale=False)
fig.show()

# Step 4: Put it all together
These previous steps are meant to be run for a given number of iterations.

In [ ]:
def KMeans(X, k, iterations=4, show_figure=False):
  #Initialize with random centroids
  indices = np.arange(X.shape[0])
  sample_indices = np.random.choice(indices, size=k, replace=False)
  means = X[sample_indices]

  #Update the distances and means
  for i in range(iterations):
    #Measure the distances with the means
    dist = distance(X, means)
    y_hat = np.argmin(dist, axis=1)

    #Forget previous means
    means = []

    #Recalculate means
    for j in range(k):
      mean = np.mean(X[y_hat==j], axis=0)
      means.append(mean)

    means = np.vstack(means)

  dist = distance(X, means)
  y_hat = np.argmin(dist, axis=1)

  if show_figure:
    fig = go.Figure()
    # Show the centroids
    fig.add_trace(go.Scatter(x = X[:,0],
                            y = X[:,1],
                            mode = 'markers',
                            marker = dict(color = y_hat),
                            showlegend = False))
    # Print the datapoints based on their current class
    fig.add_trace(go.Scatter(x = means[:,0],
                            y = means[:,1],
                            mode = 'markers',
                            marker = dict(color = 'black'),
                            showlegend = False))
    fig.show()

  return y_hat, means

In [ ]:
y_hat, means = KMeans(df1, 5, iterations=5, show_figure=True)

# How many classes?
One question that arises with this method is actually how many classes is the optimal. It is always possible to select randomly the number of clusters, or determine it by visually analyzing your data. However, is not that straightforward all the time.

One of the main methods to determine the optimal number of $k$ classes is the *Elbow method*. It consists on comparing the levels of *distortion* of each number of $k$ classes, and select the one that 'stops' the drastic change in distortion.

Distortion is the the average of the squared distances from the cluster centers of the respective clusters.Graphically, this behavior will look as an elbow, and the optimal value of $k$ will be the actual elbow.

Since this method is still more visual, there are more sophisticated methods to determine the optimal number of classes. You can see more about that [here](https://towardsdatascience.com/k-means-clustering-algorithm-applications-evaluation-methods-and-drawbacks-aa03e644b48a), [here](https://www.geeksforgeeks.org/elbow-method-for-optimal-value-of-k-in-kmeans/), and [here](https://towardsdatascience.com/elbow-method-is-not-sufficient-to-find-best-k-in-k-means-clustering-fc820da0631d#:~:text=The%20elbow%20method%20is%20a,cluster%20and%20the%20cluster%20centroid.).

In [ ]:
distortions = []
distances = []

# We´ll evaluate the first 20 clusters
for k in range(1,21):
  y_hat, means = KMeans(df1, k, iterations=5) # Fit the model with the k number of clusters

  # Get the distance between each centroid with its datapoints
  for i in range(len(df1)):
    group = y_hat[i]  # Get the corresponding class of the point
    distances.append(distance([df1[i]], [means[group]])[0][0])  # Save the distance

  distortion = sum(distances) / len(distances)  # Get the distortion
  distortions.append(distortion)  # Group the distortion on the list
  print(f"Distortion {k} clusters: {distortion}")

Distortion 1 clusters: 8.352887956098705
Distortion 2 clusters: 6.913523449290464
Distortion 3 clusters: 5.202876425503751
Distortion 4 clusters: 5.182665177205515
Distortion 5 clusters: 4.387349095185362
Distortion 6 clusters: 3.905356250517704
Distortion 7 clusters: 3.5067780279315746
Distortion 8 clusters: 3.203095135279693
Distortion 9 clusters: 2.9592990123009395
Distortion 10 clusters: 2.761547158435843
Distortion 11 clusters: 2.596274969691392
Distortion 12 clusters: 2.458014358764952
Distortion 13 clusters: 2.3403087438829173
Distortion 14 clusters: 2.233753988936394
Distortion 15 clusters: 2.1405683567107574
Distortion 16 clusters: 2.060850122781423
Distortion 17 clusters: 1.9865539334199043
Distortion 18 clusters: 1.9220878369975414
Distortion 19 clusters: 1.8620313333628904
Distortion 20 clusters: 1.8093899737903567


In [ ]:
fig = px.line(x = range(1,21),
              y = distortions,
              markers = True,
              title = 'K-Means Distortion Plot')
fig.show()

In [ ]:
# Assuming the optimal is k=3
y_hat, means = KMeans(df1, 3, iterations=20, show_figure=True)

# How efficient is the model?
As mentioned before, this method is best fitted for normally distributed data. The following datasets will exemplify how this implementation behaves on different situations.

Since our remaining datasets have a ground-truth label, it is possible to determine how good the model is for classification. We´ll use the following metrics with that purpose:



*   Accuracy: Correctly classified datapoints
*   Precision: How 'accurate' my positive predictions are
*   Recall: How efficient the model is to positively label data
*   F1-score: Metric that evaluates both precision and recall

You can have more details [here](https://medium.com/analytics-vidhya/confusion-matrix-accuracy-precision-recall-f1-score-ade299cf63cd).



In [ ]:
"""
Measure accuracy, precision, recall and F1-score.
Create a confusion matrix as well to represent the classification.

y_hat - Labels obtained from the model
y - Ground truth labels
"""
def metrics(y_hat, y):
  total = len(y)
  tn = 0 # True negative (Original and predicted = 0)
  tp = 0 # True positive (Original and predicted = 1)
  fn = 0 # False negative (Original = 1 but predicted = 0)
  fp = 0 # False positive (Original = 0 but predicted = 1)

  # Count the correct and incorrect classifications
  for i in range(len(y)):
    if y[i] == 0:
      if y_hat[i] == 0:
        tn += 1
      else:
        fp += 1
    else:
      if y_hat[i] == 0:
        fn += 1
      else:
        tp += 1

  # Get the metrics
  acc = (tp + tn) / total # Accuracy
  prec = tp / (tp + fp) # Precision
  rec = tp / (tp + fn)  # Recall
  f = 2 * ((prec * rec) / (prec + rec)) # F1-score
  print(f"Accuracy: {acc}")
  print(f"Precision: {prec}")
  print(f"Recall: {rec}")
  print(f"F1-score: {f}")
  
  # Create the confusion matrix
  fig = go.Figure()

  fig.add_trace(go.Heatmap(z = [[fp, tp], [tn, fn]],
                           x = ['False', 'True'],
                           y = ['True', 'False'],
                           text = [[f'FP:{fp}', f'TP:{tp}'], [f'TN:{tn}', f'FN:{fn}']],
                           texttemplate = '%{text}',
                           colorscale = 'blues',
                           showscale = False))
  
  fig.update_layout(title = 'Confusion Matrix',
                    yaxis_title = 'True Label',
                    xaxis_title = 'Predicted Label')
  fig.show()

In [ ]:
# Fit the donut dataset
X = np.array([[df2[0][i], df2[1][i]] for i in range(len(df2))])  # Adjust the dataset to the form our KMeans model uses
y = np.hstack(df2[2].values)
donut_y_hat, donut_means = KMeans(X, 2, iterations=20, show_figure=True)

# Get the metrics
metrics(donut_y_hat, y)

Accuracy: 0.52125
Precision: 0.5227394328517924
Recall: 0.4885
F1-score: 0.5050400620315326


In [ ]:
# Fit the xor dataset
X = np.array([[df3['x1'][i], df3['x2'][i]] for i in range(len(df3))])  # Adjust the dataset to the form our KMeans model uses
y = np.hstack(df3['y'].values)
xor_y_hat, xor_means = KMeans(X, 2, iterations=20, show_figure=True)

# Get the metrics
metrics(xor_y_hat, y)

Accuracy: 0.49925
Precision: 0.4992466097438473
Recall: 0.497
F1-score: 0.4981207717364069


# Conclusions
As you can see, when comparing the classification with actual data, this model is not that efficient since it only groups randomly each datapoint. Since this model has more or less an accuracy of 50%, it´s accuracy is almost the same as tossing a coin.

Then, this model is only useful when there is no current classification of data, and you need to group your dataset into a particular number of groups. When you know exactly which class each observation belongs, is better to use supervised learning methods.